# Metro's of the world

This notebook has a few examples of pulling Metro (Underground/Subway) networks from OpenStreetMap (OSM) and plotting them in Bokeh plots. The idea is to produce something interactive and fun to play with. In the future I might try combining the metros in a single plot for comparisons, e.g. size, stops, lines etc. For example like [this](https://www.google.com/url?sa=i&url=https%3A%2F%2Fsoranews24.com%2F2015%2F03%2F23%2Fwe-finns-just-like-it-simple-net-users-cant-get-enough-of-helsinki-metro-map%2F&psig=AOvVaw1j5fY74y3ffxBZ4UK0NaJs&ust=1628545765978000&source=images&cd=vfe&ved=0CAoQjRxqFwoTCODVjfWzovICFQAAAAAdAAAAABAD])

The code is not standardised, and I've tried a few different ways of getting the required data from OSM. For example creating a bounding box (area) and extracting subway tags, or alternatively, selecting the Metro relationship for the network and then pulling data from its members. The second approach is slower to run, but is generally more comprehensive, however, stations and lines are then a single colour and repeated for other lines on the network, rather than being combined into a single station or track.

As well as standardising a little, e.g. turning into functions, it would be good to seperate out the data, so that each metro is stored separately, rather than overwriting, making it easier to combine at a later stage.

## Setup

Import libraries and standard tools used

In [177]:
import os
import requests
import json

import openstreetmap_mapping as osm

import pandas as pd

from bokeh.plotting import show, output_file
from bokeh.io import output_notebook

from bokeh.plotting import figure
from bokeh.models import WMTSTileSource, ColumnDataSource
from bokeh.models import HoverTool
from bokeh.layouts import gridplot
from bokeh.models import Range1d


from pyproj import Transformer

output_notebook()

Loading BokehJS ...

In [2]:
%load_ext autoreload
%autoreload 2

In [132]:
area_Glasgow = "(55.82, -4.34, 55.9, -4.22)"
area_London = "(51.3426, -0.5527, 51.6726, 0.1929)"
area_Moscow = "(55.503, 37.0789,56.003, 38.1871)"
area_Budapest = "(47.4439, 18.9315, 47.5851, 19.1711)"
area_Paris = "(48.744, 2.1265, 49.0316, 2.6099)"
area_NewYork = "(40.4924, -74.2669, 40.9566, -73.5631)"
area_Tokyo = "(35.4366, 139.4357, 36.0413, 140.1402)"
area_Beijing = "(39.6512, 115.9181, 40.2124, 116.7943)"
area_Helsinki = "(60.1278, 24.7041, 60.3511, 25.18)"

In [4]:
MAP_TILES = {"OpenMap": WMTSTileSource(url="http://c.tile.openstreetmap.org/{Z}/{X}/{Y}.png"),
         "ESRI": WMTSTileSource(url="https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{Z}/{Y}/{X}.jpg"),
         "OpenTopoMap": WMTSTileSource(url="https://tile.opentopomap.org/{Z}/{X}/{Y}.png")}

In [5]:
# Use pyproj to transform longitude and latitude into web-mercator and add to a copy of the asset dataframe
TRANSFORM_4326_TO_3857 = Transformer.from_crs("EPSG:4326", "EPSG:3857")
 

In [6]:
# Place to save data so that the number of OSM requests are reduced when re-loading the same data
path_save = r"data/metro/"

if not os.path.exists(path_save):
    os.makedirs(path_save)
    

In [88]:
def get_subway(area="(55.503, 37.0789,56.003, 38.1871)"):

    key = "railway"
    tag = "subway"
    recursion = ""
    output = "geom"

    data = osm.toolkit.get_osm_data(key=key,
                                    tag=tag,
                                    area=area,
                                    output="geom",
                                    recursion="",
                                    element="way")
    
    return data

In [196]:
def plot_subway(data,output_file_name='subway.html',line_color='red'):


    # create a plot of the subway system    
    output_file(output_file_name)

    p = figure(plot_width=800, plot_height=800,
              x_axis_type="mercator", y_axis_type="mercator")

    # p.add_tile(MAP_TILES['ESRI'])

    tooltips = [("id", "@id"),
                ("name", "@name"),
                ("line", "@line"),
                ("network", "@network"),
                ("operator", "@operator"),
                ("(lat,lon)", "@coordinates")]

    xx = list()
    yy = list()
    for cnt,way in data.iterrows():


        xxx,yyy = TRANSFORM_4326_TO_3857.transform(list(pd.DataFrame.from_records(way['geometry'])['lat']),
                                                 list(pd.DataFrame.from_records(way['geometry'])['lon']))

        xx.append(xxx)
        yy.append(yyy)


    source = ColumnDataSource({'xs':xx,'ys':yy})

    p.multi_line('xs',
                 'ys',
                 source=source,
                 line_width=2,
                 line_color=line_color,
          )

    p.xaxis.visible = False
    p.xgrid.visible = False
    
    p.yaxis.visible = False
    p.ygrid.visible = False
        
    central_x = max(max(xx)) - min(min(xx))
    central_y = max(max(yy)) - min(min(yy))
    p.x_range=Range1d(central_x-50000, central_x+50000)
    p.y_range=Range1d(central_y-50000, central_y+50000)
    
    return p

In [193]:
min(min(xx))

4155342.690911343

In [194]:
max(max(xx))

4222908.478862386

In [195]:
max(max(xx)) - min(min(xx))

67565.78795104334

## Glasgow's Clockwork Orange

In [197]:
data = get_subway(area_Glasgow)

In [198]:
glasgow = plot_subway(data,output_file_name='subway.html',line_color='orange')

In [199]:
show(glasgow)

## Moscow Metro

In [144]:
data = get_subway(area_Moscow)

In [145]:
moscow = plot_subway(data,output_file_name='subway.html',line_color='red')

In [146]:
show(moscow)

## Budapest Metro

In [147]:
area_Glasgow = "(55.82, -4.34, 55.9, -4.22)"
area_London = "(51.3426, -0.5527, 51.6726, 0.1929)"
area_Moscow = "(55.503, 37.0789,56.003, 38.1871)"
area_Budapest = "(47.4439, 18.9315, 47.5851, 19.1711)"
area_Paris = "(48.744, 2.1265, 49.0316, 2.6099)"

In [148]:
data = get_subway(area_Budapest)

In [149]:
budapest = plot_subway(data,output_file_name='subway.html',line_color='black')

In [150]:
show(budapest)

## Paris Metro

In [151]:
data = get_subway(area_Paris)

In [152]:
paris = plot_subway(data,output_file_name='subway.html',line_color='blue')

In [153]:
show(paris)

## London Underground

In [173]:
data = get_subway(area_London)

In [174]:
london = plot_subway(data,output_file_name='subway.html',line_color='blue')

In [175]:
show(london)

## New York Metro

In [157]:
data = get_subway(area_NewYork)

In [158]:
newYork = plot_subway(data,output_file_name='subway.html',line_color='blue')

In [159]:
show(newYork)

## Tokyo

In [160]:
data = get_subway(area_Tokyo)

In [161]:
tokyo = plot_subway(data,output_file_name='subway.html',line_color='red')

In [162]:
show(tokyo)

## Beijing

In [164]:
data = get_subway(area_Beijing)

In [165]:
beijing = plot_subway(data,output_file_name='subway.html',line_color='red')

In [166]:
show(beijing)

## Helsinki

In [167]:
data = get_subway(area_Helsinki)

In [168]:
helsinki = plot_subway(data,output_file_name='subway.html',line_color='red')

In [169]:
show(helsinki)

## All together now

In [176]:
# make a grid
grid = gridplot([[glasgow, moscow, budapest], [newYork, tokyo, paris], [london, beijing, helsinki]], plot_width=250, plot_height=250)

show(grid)